# Lesson 1: Writing like your favorite author

In this lesson, aimed to be of introductory nature, we shall start by something easy: word prediction. The idea is to use an entire book to teach the machine which words show up sequentially. The main tool is a classical mathematical object: Markov chains.

## I. Loading books from the Project Gutenberg (https://www.gutenberg.org)

In [6]:
from __future__ import print_function
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

#List of books along with their identifier on Project Gutenberg
# Feel free to expand the list and pick your favorite
books = { "Alice's Adventures in Wonderland": 11  , # by Lewis Carroll, 160 kb
          "The Complete Poetical Works of Edgar Allan Poe": 10031, #by Edgar Allan Poe, 400 kb
          "The Hound of the Baskervilles":    2852, # by Sir Conan Doyle, 340 kb
          "The King James Bible":             10,   # by King James, 4.3 Mb
          "The Complete Works of William Shakespeare": 100 #by William Shakespeare, 5.5 Mb
        }

def bookSelection(bookTitle):
    bookId = books[bookTitle]
    #
    print( "Loading text from Project Gutenberg URL..." )
    import urllib3
    http = urllib3.PoolManager()
    # url = 'https://www.gutenberg.org/cache/epub/%s/pg%s.txt' % (bookId, bookId) # old url, website has changed
    url = 'https://www.gutenberg.org/files/%s/%s-0.txt' % (bookId, bookId)
    request = http.request('GET', url)
    #
    global book
    book = request.data
    print( "Request done with %d bytes..." % len(book))
    #Converts from bytes to string
    book = book.decode("utf-8") 
    return

interact(bookSelection, bookTitle=books.keys() );


Widget Javascript not detected.  It may not be installed or enabled properly.


In [14]:
print(book[534:2000])



Title: Alice’s Adventures in Wonderland

Author: Lewis Carroll

Release Date: June 25, 2008 [EBook #11]
[Most recently updated: October 12, 2020]

Language: English

Character set encoding: UTF-8

*** START OF THIS PROJECT GUTENBERG EBOOK ALICE’S ADVENTURES IN WONDERLAND ***



Produced by Arthur DiBianca and David Widger

[Illustration]




Alice’s Adventures in Wonderland

by Lewis Carroll

THE MILLENNIUM FULCRUM EDITION 3.0

Contents

 CHAPTER I.     Down the Rabbit-Hole
 CHAPTER II.    The Pool of Tears
 CHAPTER III.   A Caucus-Race and a Long Tale
 CHAPTER IV.    The Rabbit Sends in a Little Bill
 CHAPTER V.     Advice from a Caterpillar
 CHAPTER VI.    Pig and Pepper
 CHAPTER VII.   A Mad Tea-Party
 CHAPTER VIII.  The Queen’s Croquet-Ground
 CHAPTER IX.    The Mock Turtle’s Story
 CHAPTER X.     The Lobster Quadrille
 CHAPTER XI.    Who Stole the Tarts?
 CHAPTER XII.   Alice’s Evidence




CHAPTER I.
Down the Rabbit-Hole


Alice was beginning to get very tired of sitting by her

In [15]:
import re #Rational expressions
words = re.split('[^A-Za-z]+', book.lower())
words = [w for w in words if w!=''] # Remove empty strings

# Computes a dictionary where keys are words
#  and values are the number of occurrences.
# Output is sorted
def generate1gram():
    gram = dict()
    
    # Populate 1-gram dictionary
    for i in range(len(words)-1):
        key = words[i]
        if gram.get(key) is None:
            gram[key] = 1
        else:
            gram[key] += 1
    
    #Warning! sorted forms a list
    gram = sorted(gram.items(), key=lambda x:-x[1])
    
    return dict(gram)

gram1 = generate1gram()

# Print length of list
print( "Total number of words, with repetition:    ", len(words) )
print( "Total number of words, without repetition: ", len(gram1) )

Total number of words, with repetition:     30618
Total number of words, without repetition:  3021


## II. Autocompletion using 1-grams

In [16]:
from IPython.display import display

# Information labels
infoLabel1 = widgets.Label(value="Input:")
infoLabel2 = widgets.Label(value="Last word:")
infoLabel3 = widgets.Label(value="Autocomplete suggestion:")
#Input area
inputArea = widgets.Textarea(
    value='',
    placeholder='Type something',
    description='',
    disabled=False
)
# Output labels
outputLastWord = widgets.Label(value='')
outputLabel = widgets.Label(value='')
output = widgets.Output()

def findLastWord(str):
    str = str.lower()
    str = str.rstrip()
    # Find last word
    # Hint: Use https://docs.python.org/3.7/library/stdtypes.html?highlight=rfind#str.rfind
    lastWordIndex = str.rfind( ' ', 0, len(str))
    lastWord = ''
    if lastWordIndex == -1:
        return str
    else:
        return str[(lastWordIndex+1):]   

def onChange(change):
    with output:
        lastWord = findLastWord(change.new)
        outputLastWord.value = lastWord
        #
        #Either the last word exists in the dictionary and then nothing to do
        possibleWords = [ (w,x) for (w,x) in gram1.items() if w.startswith(lastWord)]
        outputLabel.value = ''.join( [ (w+'(%d) ')%x for (w,x) in possibleWords ] )

# Sets a callback upon the change of the TextArea's content
inputArea.observe(onChange, 'value')

display( infoLabel1, output)
display( inputArea, output)
display( widgets.HBox([infoLabel2, outputLastWord]), output)
display( infoLabel3, output)
display( outputLabel, output)

Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


## III. Predicting the next word: 2-grams

In [17]:
# Computes a dictionary where keys are all pairs of words
#  and values are the number of occurrences.
# Output is sorted
def generate2gram():
    gram = dict()
    
    # Populate 2gram dictionary
    for i in range(len(words)-1):
        key = ( words[i], words[i+1] )
        if gram.get(key) is None:
            gram[key] = 1
        else:
            gram[key] += 1
    
    #Warning sorted forms a list
    gram = sorted(gram.items(), key=lambda x:-x[1])
    
    return dict(gram)

In [18]:
#Test
gram2 = generate2gram()
print( [(w,x) for (w,x) in gram2.items() if x>50] )

[(('said', 'the'), 210), (('of', 'the'), 163), (('said', 'alice'), 116), (('in', 'a'), 102), (('in', 'the'), 99), (('project', 'gutenberg'), 88), (('and', 'the'), 86), (('to', 'the'), 85), (('it', 'was'), 76), (('the', 'queen'), 73), (('at', 'the'), 63), (('the', 'king'), 62), (('as', 'she'), 61), (('don', 't'), 61), (('a', 'little'), 60), (('she', 'had'), 60), (('i', 'm'), 59), (('mock', 'turtle'), 57), (('it', 's'), 57), (('gutenberg', 'tm'), 57), (('she', 'was'), 55), (('and', 'she'), 55), (('the', 'mock'), 54), (('to', 'be'), 54), (('the', 'gryphon'), 53), (('with', 'the'), 52), (('the', 'hatter'), 52)]


In [19]:
from IPython.display import display

# Information labels
infoLabel1 = widgets.Label(value="Input:")
infoLabel2 = widgets.Label(value="Autocomplete suggestions:")
infoLabel3 = widgets.Label(value="Suggestion from word prediction:")
#Input area
inputArea = widgets.Textarea(
    value='',
    placeholder='Type something',
    description='',
    disabled=False
)
# Output labels
outputAutocomplete = widgets.Label(value='')
outputPrediction = widgets.Label(value='')
output = widgets.Output()

def onChange(change):
    with output:
        lastWord = findLastWord( change.new )
        #
        # Autocomplete as before
        possibleWords = [ (w,x) for (w,x) in gram1.items() if w.startswith(lastWord)]
        outputAutocomplete.value = ''.join( [ w+'(%d) '%x for (w,x) in possibleWords ] )
        #
        # Prediction
        # Either the last word does not exist in the dictionary (or equivalently the 1-gram) and then nothing to do
        if lastWord not in [w for (w,x) in possibleWords]:
            outputPrediction.value = ''
        # or the last word allows to predict the next
        else:
            possiblePairs = predictNextWord(lastWord)
            outputPrediction.value = ''.join( [ (p[1]+'(%d) ') % x for (p,x) in possiblePairs ] )
        
def predictNextWord(str):
    return [ i for i in gram2.items() if str==i[0][0]]

# Sets a callback upon the change of the TextArea's content
inputArea.observe(onChange, 'value')

display( widgets.HBox( [infoLabel1, inputArea] ) , output)
display( infoLabel2, output)
display( outputAutocomplete, output)
display( infoLabel3, output )
display( outputPrediction, output)


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


Widget Javascript not detected.  It may not be installed or enabled properly.


# III. N-Grams (tri-grams and more...)

In [20]:
def generateNgram(n=1):
    gram = dict()
    
    # Some helpers to keep us crashing the PC for now
    assert n > 0 and n < 100
    
    # Populate N-gram dictionary
    for i in range(len(words)-(n-1)):
        key = tuple(words[i:i+n])
        if gram.get(key) is None:
            gram[key] = 1
        else:
            gram[key] += 1
            
    #Warning sorted forms a list
    gram = sorted(gram.items(), key=lambda x:-x[1])
    return dict(gram)

In [21]:
# Test
gram5 = generateNgram(5)
print( [(w,x) for (w,x) in gram5.items() if x>10] )

[(('the', 'project', 'gutenberg', 'literary', 'archive'), 13), (('project', 'gutenberg', 'literary', 'archive', 'foundation'), 13), (('project', 'gutenberg', 'tm', 'electronic', 'works'), 12)]


In [22]:
maxLag = 5
Ngrams = []
for i in range(1,maxLag):
    Ngrams.append( generateNgram(i))
Ngrams.reverse()
print( "Generated Ngrams for N from 1 to ", len(Ngrams) )

Generated Ngrams for N from 1 to  4


In [23]:
def findLastWords(str, count=1):
    if count<= 0:
        return []
    str = str.lower()
    str = str.rstrip()
    #
    lastWordIndex = str.rfind( ' ', 0, len(str))
    lastWord = ''
    if lastWordIndex == -1:
        return [str]
    else:
        rec = findLastWords(str[:lastWordIndex], count-1)
        rec.append( str[(lastWordIndex+1):] )
        return rec

def predict(str):
    choices = []
    for gram in Ngrams:
        choice_i = [ (w,x) for (w,x) in gram.items() if w[:-1] == tuple( str[(len(str)-len(w)+1):] )]
        choices.append( choice_i )
    return choices

def predictMaxLag(str):
    for gram in Ngrams:
        choice = [ (w,x) for (w,x) in gram.items() if w[:-1] == tuple( str[(len(str)-len(w)+1):] )]
        if choice != []:
            return choice
    return []

import random
def weighted_choice(choice):
   total = sum(w for c, w in choice)
   r = random.uniform(0, total)
   upto = 0
   for c, w in choice:
      if upto + w > r:
         return c
      upto += w
    
    
def generate(str):
    choice = predictMaxLag(str)
    value = weighted_choice(choice)
    return value[-1]

In [24]:
str = findLastWords( "kinf of the jungle and of the wild", count=3)
print( str )
print("")
gen = generate(str)
print(gen)

['of', 'the', 'wild']

beast


In [25]:
a = list( Ngrams[0] )
print(a[:50])

[('said', 'the', 'mock', 'turtle'), ('project', 'gutenberg', 'tm', 'electronic'), ('she', 'said', 'to', 'herself'), ('the', 'project', 'gutenberg', 'tm'), ('the', 'project', 'gutenberg', 'literary'), ('project', 'gutenberg', 'literary', 'archive'), ('gutenberg', 'literary', 'archive', 'foundation'), ('gutenberg', 'tm', 'electronic', 'works'), ('a', 'minute', 'or', 'two'), ('in', 'the', 'united', 'states'), ('you', 'won', 't', 'you'), ('terms', 'of', 'this', 'agreement'), ('said', 'the', 'march', 'hare'), ('will', 'you', 'won', 't'), ('project', 'gutenberg', 'tm', 'license'), ('the', 'terms', 'of', 'this'), ('of', 'project', 'gutenberg', 'tm'), ('of', 'the', 'project', 'gutenberg'), ('said', 'alice', 'in', 'a'), ('i', 'don', 't', 'know'), ('to', 'the', 'project', 'gutenberg'), ('alice', 's', 'adventures', 'in'), ('s', 'adventures', 'in', 'wonderland'), ('as', 'well', 'as', 'she'), ('well', 'as', 'she', 'could'), ('in', 'a', 'great', 'hurry'), ('in', 'a', 'tone', 'of'), ('the', 'moral', 

In [26]:
length=24
str = ''
for i in range(1,length):
    end = findLastWords(str, count=3)
    nextWord = generate(end)
    str = str + ' ' + nextWord
    print(str)

 they
 they sat
 they sat down
 they sat down and
 they sat down and began
 they sat down and began to
 they sat down and began to repeat
 they sat down and began to repeat it
 they sat down and began to repeat it when
 they sat down and began to repeat it when a
 they sat down and began to repeat it when a cry
 they sat down and began to repeat it when a cry of
 they sat down and began to repeat it when a cry of the
 they sat down and began to repeat it when a cry of the trial
 they sat down and began to repeat it when a cry of the trial stupid
 they sat down and began to repeat it when a cry of the trial stupid things
 they sat down and began to repeat it when a cry of the trial stupid things alice
 they sat down and began to repeat it when a cry of the trial stupid things alice began
 they sat down and began to repeat it when a cry of the trial stupid things alice began in
 they sat down and began to repeat it when a cry of the trial stupid things alice began in a
 they sat down and

# IV. Conclusion

- N-grams are certainly useful for autocompletion
- It is simple. Markov chains date back to 1913
- Certainly too simple: For word prediction geared toward generating text, it does not seem very robust nor endowed with semantics